# Transaction Fees on Nomos

In [1]:
%load_ext autoreload
%autoreload 2

import plotly.express as px
import pandas as pd
pd.options.plotting.backend = "plotly"
from simulation import run_simulation
from simulation_parameters import SimulationParameters
from tx_fees_models import PROTOCOL_CONSTANTS

In [2]:
days = 1

In [3]:
demand = 5000

std_dev = 0.01/100.
variable_gas_limits = True
below_gas_limit = 0.5

In [4]:
params = SimulationParameters(
    num_blocks=int(days * 24 * 60 * 60 / 12),  # number of blocks in "days",
    demand_sizes=[demand],  # very low, normal, very high demand
    demand_probabilities=[1.],  # they must sum to 1
    fee_cap_range=(0., std_dev),  # in percentage, mean and std deviation
    max_tip_pct=0,  # this only affects the EIP-1559 simulation
    scale_block_size=0.05,
    probability_stop_below_gas_limit=below_gas_limit,
    purge_after=4,
    variable_gas_limits=variable_gas_limits
)

In [ ]:
df_stats_merged, df_chain_stats_merged = run_simulation(params)

In [ ]:
df_stats_merged[["price_StableFee", "price_EIP"]].plot(
    title=f'''
StableFee vs EIP-1559 - {demand} txs -
{"variable" if variable_gas_limits else "fixed"} gas/tx -
{std_dev * 100:.2e}% standard deviation - 
{below_gas_limit * 100:.2f}% chance to stop below gas limit
''',
)

In [ ]:
df_stats_merged[["num_tx_EIP", "num_tx_StableFee"]].plot()

In [ ]:
df_stats_merged[["tot_paid_EIP", "tot_paid_StableFee"]].plot()

In [ ]:
df_stats_merged[["demand_size_EIP"]].plot.bar()

In [ ]:
(df_stats_merged["num_tx_EIP"].sub(df_stats_merged["num_tx_StableFee"]) > 0).value_counts()

In [ ]:
df_chain_stats_merged[["tot_gas_used_EIP", "tot_gas_used_StableFee"]].plot()

In [ ]:
fig = df_chain_stats_merged["tot_gas_used_EIP"].plot.bar()
fig.add_shape(
    type="line",
    x0=0,
    y0=PROTOCOL_CONSTANTS["TARGET_GAS_USED"],
    x1=len(df_chain_stats_merged),
    y1=PROTOCOL_CONSTANTS["TARGET_GAS_USED"],
    line=dict(color="red", width=2)
)

fig.show()